In [1]:
import pandas as pd

df = pd.read_csv("example_dataset.csv")
df.head()

PDB                                            Epitope
0  5VX4  A:GLN:148, A:PHE:122, A:ASP:192, A:ASN:125, A:...
1  5F4J  A:THR:485, A:LEU:527, A:SER:526, A:SER:519, A:...
2  4E9O  X:SER:64, X:LEU:203, X:THR:35, X:ASN:175, X:AS...
3  6H3S  B:TYR:612, B:HIS:616, B:THR:582, B:GLY:615, B:...
4  1OQE  L:CYS:9, L:HIS:16, L:CYS:20, L:LEU:12, L:VAL:1...

In [2]:
import pickle

with open("example_label_dict.pkl", "rb") as f:
     y_example = pickle.load(f)

In [3]:
with open("example_pssm.pkl", "rb") as f:
     example_pssm = pickle.load(f)

In [4]:
with open("example_nonsym_graphs_5A.pkl", "rb") as f:
    example_graphs = pickle.load(f)

To use the Graphein submodule graphein.protein.features.sequence.embeddings, you need to install: biovec 
biovec cannot be installed via conda
DEBUG:matplotlib:matplotlib data path: /home/sjchoi/anaconda3/envs/torch/lib/python3.8/site-packages/matplotlib/mpl-data
DEBUG:matplotlib:CONFIGDIR=/home/sjchoi/.config/matplotlib
DEBUG:matplotlib:interactive is False
DEBUG:matplotlib:platform is linux
DEBUG:matplotlib:loaded modules: ['sys', 'builtins', '_frozen_importlib', '_imp', '_warnings', '_io', 'marshal', 'posix', '_frozen_importlib_external', '_thread', '_weakref', 'time', 'zipimport', '_codecs', 'codecs', 'encodings.aliases', 'encodings', 'encodings.utf_8', '_signal', '__main__', 'encodings.latin_1', '_abc', 'abc', 'io', '_stat', 'stat', '_collections_abc', 'genericpath', 'posixpath', 'os.path', 'os', '_sitebuiltins', '_locale', '_bootlocale', 'types', 'importlib._bootstrap', 'importlib._bootstrap_external', 'warnings', 'importlib', 'importlib.machinery', 'importlib.abc', '_operator', 

DEBUG:matplotlib:CACHEDIR=/home/sjchoi/.cache/matplotlib
DEBUG:matplotlib.font_manager:Using fontManager instance from /home/sjchoi/.cache/matplotlib/fontlist-v330.json
DEBUG:matplotlib.pyplot:Loaded backend module://matplotlib_inline.backend_inline version unknown.
DEBUG:matplotlib.pyplot:Loaded backend module://matplotlib_inline.backend_inline version unknown.
To do so, use the following command: conda install -c pytorch3d pytorch3d
To do so, use the following command: conda install -c pytorch3d pytorch3d


In [5]:
with open("example_psaia.pkl", "rb") as f:
     example_psaia = pickle.load(f)

In [6]:
import torch.nn.functional as F

def normalize(d, max_val, min_val):
    d = float(d)
    norm = (d - min_val) / (max_val - min_val)
    return norm

def distance_bond(d):
    num = 0
    if "distance_threshold" in list(d['kind']):
        num = 1
    return num

def one_hot(ss):
    dssp_ss = {"H":0, "B":1, "E":2, "G":3, "I":4, "T":5, "S":6, "-":7}
    dssp_num = dssp_ss[ss]

    one_hot_mat = np.array(F.one_hot(torch.arange(8), num_classes=8))
    one_hot_enc = one_hot_mat[dssp_num]
    return one_hot_enc

In [7]:
from graphein.protein.config import ProteinGraphConfig

config = ProteinGraphConfig()

In [9]:
## after 

from graphein.protein.subgraphs import extract_subgraph_from_point
from Bio.PDB.DSSP import dssp_dict_from_pdb_file, residue_max_acc
from graphein.ml.conversion import GraphFormatConvertor
from graphein.protein.utils import download_pdb

import torch
import numpy as np
import pandas as pd
import random
import numpy as np


aa_dict = {'CYS': 'C', 'ASP': 'D', 'SER': 'S', 'GLN': 'Q', 'LYS': 'K',
         'ILE': 'I', 'PRO': 'P', 'THR': 'T', 'PHE': 'F', 'ASN': 'N', 
         'GLY': 'G', 'HIS': 'H', 'LEU': 'L', 'ARG': 'R', 'TRP': 'W', 
         'ALA': 'A', 'VAL':'V', 'GLU': 'E', 'TYR': 'Y', 'MET': 'M'}

def format_convert_surface(graphs_list, y, df, pssm, psaia, RSA):
    format_convertor = GraphFormatConvertor('nx', 'pyg',
                                            verbose = 'gnn',
                                            columns = None)
    # NBVAL_SKIP
    pyg_list = [format_convertor(graph) for graph in graphs_list]
    
    ## building amino acid composition features
    n_comp_list = []
    n_sg_len_list = []
    
    ## building dssp features (rsa, ss)
    n_asa_list = []
    n_ss_list = []
    n_phi_list = []
    n_psi_list = []
    for idx, g in enumerate(pyg_list): 
        aaindex1(graphs_list[idx], 'FAUJ880101') # Steric parameter (graph shape index)
        aaindex1(graphs_list[idx], 'CHAM820101') # Polarizability   
        aaindex1(graphs_list[idx], 'FAUJ880103') # Volume (normalized van der Waals volumn) 
        aaindex1(graphs_list[idx], 'ZIMJ680101') # Hydrophobicity
        aaindex1(graphs_list[idx], 'ZIMJ680104') # Isoelectric point
        aaindex1(graphs_list[idx], 'CHOP780201') # Helix probability
        aaindex1(graphs_list[idx], 'CHOP780202') # Sheet probability
        aaindex1(graphs_list[idx], 'CHOP780203') # Turn probability
        aaindex1(graphs_list[idx], 'ZIMJ680103') # Polarity
        
        esm_residue_embedding(graphs_list[idx]) # input of node embedding esm (1280 dim)
        
        ## building amino acid composition features
        
        aa_count_list = []
        sg_len_list = []
        for n, d in graphs_list[idx].nodes(data=True):
            radius = 8
            sg = extract_subgraph_from_point(graphs_list[idx], centre_point=tuple(d['coords']), radius=radius)
            sg_len_list.append(len(sg.nodes))
            
            aa_count = {'C': 0, 'D': 0, 'S': 0, 'Q': 0, 'K': 0,
                        'I': 0, 'P': 0, 'T': 0, 'F': 0, 'N': 0, 
                        'G': 0, 'H': 0, 'L': 0, 'R': 0, 'W': 0, 
                        'A': 0, 'V': 0, 'E': 0, 'Y': 0, 'M': 0}
            
            for n, d in sg.nodes(data=True):
                aa = aa_dict[d["residue_name"]]
                aa_count[aa] += 1
            aa_count_list.append(aa_count)
        n_comp_list.append(aa_count_list)
        n_sg_len_list.append(sg_len_list)        

        
        ## building dssp features (rsa, ss)
        
        pdb = download_pdb(config=config, pdb_code=graphs_list[idx].graph['pdb_id']) 
        dssp = dssp_dict_from_pdb_file(pdb)

        asa_list = []
        ss_list = []
        phi_list = []
        psi_list = []
        
        
        for n, d in graphs_list[idx].nodes(data=True):
            
            try:
                key = (d["chain_id"], (' ', d['residue_number'], ' '))
                ss_list.append(dssp[0][key][1])
                asa_list.append(dssp[0][key][2])
                phi_list.append(dssp[0][key][3])
                psi_list.append(dssp[0][key][4])
            except:
                ss_list.append("-")
                asa_list.append(0)
                phi_list.append(0)
                psi_list.append(0)
                print("Key Error... appending ss: -, asa: 0, phi: 0, psi: 0")
        n_asa_list.append(asa_list)
        n_ss_list.append(ss_list)
        n_phi_list.append(phi_list)
        n_psi_list.append(psi_list)

        
        # features   1. amino_acid type (one-hot)  (dim=20)
        #            2. Steric parameter (graph shape index) (max-min normalize)
        #            3. Polarizability     (max-min normalize)              
        #            4. Volume (normalized van der Waals volumn) (standardization) 
        #            5. Hydrophobicity (max-min normalize) 
        #            6. Isoelectric point (standardization)   
        #            7. Helix probability
        #            8. Sheet probability
        #            9. Turn probability
        #            10. Polarity (standardization) 
        #            11. B-factor
        #            12. RSA
        #            11. phi angle  
        #            12. psi angle  
        #            13. protrusion index  # thinking of adding. not yet!
        #            14. residue depth    # thinking of adding. not yet!
        #            15. pssm (max-min normalize) (dim=20) 
        #            16. a.a. composition (dim=20)
        #            17. secondary structure (ont-hot) (dim=8)

        ## re-scaling including esm embedding 
        try:
            g.node_attrs = torch.tensor(np.concatenate([np.array([d['amino_acid_one_hot'] for n, d in graphs_list[idx].nodes(data=True)]),
                                                          np.array([[normalize(d['aaindex1_FAUJ880101'], 4.19, 0), normalize(d['aaindex1_CHAM820101'], 0.409, 0), 
                                                          normalize(d['aaindex1_FAUJ880103'], 8.08, 0), normalize(d['aaindex1_ZIMJ680101'], 3.07, 0), 
                                                          normalize(d['aaindex1_ZIMJ680104'], 10.76 , 2.77), normalize(d['aaindex1_CHOP780201'], 1.51, 0.57),
                                                          normalize(d['aaindex1_CHOP780202'], 1.7, 0.37), normalize(d['aaindex1_CHOP780203'], 1.56, 0.47),
                                                          normalize(d['aaindex1_ZIMJ680103'], 52.0, 0), normalize(d['b_factor'], 459.9, 0),
                                                          normalize(n_asa_list[idx][index] / residue_max_acc["Sander"][d['residue_name']], 1.72, 0),
                                                          normalize(n_phi_list[idx][index], 180, -180), normalize(n_psi_list[idx][index], 180, -180),
                                                          normalize(psaia[idx][(psaia[idx]['chainid'] == d['chain_id']) & (psaia[idx]['resid'] == str(d['residue_number']))]["averageCX"], 10, 0),
                                                          normalize(psaia[idx][(psaia[idx]['chainid'] == d['chain_id']) & (psaia[idx]['resid'] == str(d['residue_number']))]["averageDPX"], 10, 0)] for index, (n, d) in enumerate(graphs_list[idx].nodes(data=True))]),
                                                          np.array(list([(np.array(pssm[idx].loc[index]).astype(np.float32) + 15) / 30 for index, (n, d) in enumerate(graphs_list[idx].nodes(data=True))])),
                                                          np.array(list([np.array(list(n_comp_list[idx][index].values())).astype(np.float32)  / n_sg_len_list[idx][index] for index, (n, d) in enumerate(graphs_list[idx].nodes(data=True))])),
                                                          np.array(list([one_hot(n_ss_list[idx][index]) for index, (n, d) in  enumerate(graphs_list[idx].nodes(data=True))])),
                                                          np.array([d["esm_embedding"] + 9.24 / 13.78 for n, d in graphs_list[idx].nodes(data=True)])], axis=1), dtype=torch.float32)
        except:
            print("wrong PDB", g.graphs_list[idx].name)
        
        g.y = torch.tensor([y[idx][n] for n, d in graphs_list[idx].nodes(data=True)])
        g.edge_attrs = torch.tensor([distance_bond(d) for u, v, d in graphs_list[idx].edges(data=True)], dtype=torch.float32)
        g.coords = torch.FloatTensor([d['coords'] for n, d in graphs_list[idx].nodes(data=True)])  
        
        ## added index that covers df
        epitope_list = df['Epitope'].values[idx].split(", ")
        
        non_epitope_list = []
        for index, (n, d) in enumerate(graphs_list[idx].nodes(data=True)):
            if (n_asa_list[idx][index] / residue_max_acc["Sander"][d['residue_name']] > RSA) & (n not in epitope_list):
                non_epitope_list.append(n)

        g.train_mask = torch.tensor([(n in epitope_list) | (n in non_epitope_list) for n, d in graphs_list[idx].nodes(data=True)])
        
    for i in pyg_list:
        if i.coords.shape[0] == len(i.node_id):
            pass
        else:
            print(i)
            pyg_list.remove(i)    
            
    return pyg_list

In [10]:
RSA = 0.15
example_pyg_list = format_convert_surface(example_graphs, y_example, df, example_pssm, example_psaia, RSA)

Using cache found in /home/sjchoi/.cache/torch/hub/facebookresearch_esm_main
DEBUG:graphein.protein.subgraphs:Found 3 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['A:SER:63', 'A:GLY:62', 'A:ILE:64'].
DEBUG:graphein.protein.subgraphs:Found 4 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['A:SER:63', 'A:LEU:65', 'A:GLY:62', 'A:ILE:64'].
DEBUG:graphein.protein.subgraphs:Found 5 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['A:SER:63', 'A:LEU:65', 'A:GLY:62', 'A:ASP:66', 'A:ILE:64'].
DEBUG:graphein.protein.subgraphs:Found 8 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['A:ILE:206', 'A:SER:63', 'A:LEU:65', 'A:ASP:66', 'A:TYR:205', 'A:ILE:207', 'A:GLY:67', 'A:ILE:64'].
DEBUG:graphein.protein.subgraphs:Found 8 nodes in the spatial point-radius subgr

DEBUG:graphein.protein.subgraphs:Found 12 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['A:SER:95', 'A:GLU:94', 'A:HIS:201', 'A:VAL:105', 'A:ILE:199', 'A:VAL:91', 'A:VAL:92', 'A:ALA:104', 'A:TYR:93', 'A:ILE:106', 'A:ILE:198', 'A:ILE:200'].
DEBUG:graphein.protein.subgraphs:Found 15 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['A:SER:95', 'A:GLU:94', 'A:THR:96', 'A:TRP:102', 'A:LEU:121', 'A:THR:103', 'A:VAL:105', 'A:ILE:199', 'A:VAL:91', 'A:VAL:92', 'A:ALA:104', 'A:TYR:93', 'A:ILE:198', 'A:PHE:122', 'A:ILE:200'].
DEBUG:graphein.protein.subgraphs:Found 13 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['A:SER:95', 'A:GLU:94', 'A:THR:96', 'A:TRP:102', 'A:THR:103', 'A:ILE:196', 'A:SER:197', 'A:ILE:199', 'A:ALA:104', 'A:ILE:198', 'A:TYR:93', 'A:ASN:97', 'A:PHE:101'].
DEBUG:graphein.protein.subgraphs:Found 13 n

DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['A:GLN:118', 'A:GLY:123', 'A:LEU:121', 'A:TYR:119', 'A:PHE:122', 'A:GLU:124', 'A:VAL:91', 'A:ASN:125', 'A:VAL:120', 'A:LYS:126'].
DEBUG:graphein.protein.subgraphs:Found 11 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['A:GLU:94', 'A:GLY:123', 'A:LEU:121', 'A:TYR:119', 'A:PHE:122', 'A:GLU:124', 'A:VAL:91', 'A:ALA:104', 'A:ASN:125', 'A:VAL:120', 'A:LYS:126'].
DEBUG:graphein.protein.subgraphs:Found 6 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['A:GLU:94', 'A:GLY:123', 'A:LEU:121', 'A:PHE:122', 'A:GLU:124', 'A:VAL:120'].
DEBUG:graphein.protein.subgraphs:Found 6 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['A:GLY:123', 'A:LEU:121', 'A:PHE:122', 'A:GLU:124', 'A:ASN:125', 'A:VAL:120'].
DEBUG:graphein.protein.subgraphs:Found 7 nodes in the spati

embedding shape (162, 1280)
embedding_total.shape (162, 1280)


DEBUG:graphein.protein.subgraphs:Found 14 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['A:THR:158', 'A:THR:156', 'A:LYS:138', 'A:PHE:139', 'A:LEU:157', 'A:ASN:132', 'A:LYS:136', 'A:ALA:107', 'A:VAL:108', 'A:PHE:140', 'A:TRP:137', 'A:PRO:110', 'A:GLU:109', 'A:SER:159'].
DEBUG:graphein.protein.subgraphs:Found 14 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['A:THR:158', 'A:THR:156', 'A:VAL:105', 'A:PHE:139', 'A:LEU:157', 'A:GLU:141', 'A:ALA:107', 'A:VAL:108', 'A:ILE:106', 'A:TRP:137', 'A:PHE:140', 'A:VAL:164', 'A:LYS:138', 'A:SER:159'].
DEBUG:graphein.protein.subgraphs:Found 14 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['A:ASN:153', 'A:THR:156', 'A:VAL:105', 'A:PHE:139', 'A:LEU:157', 'A:GLU:141', 'A:ALA:107', 'A:VAL:108', 'A:ILE:106', 'A:PHE:140', 'A:ARG:154', 'A:LYS:138', 'A:MET:142', 'A:ARG:155'].
D

...

DEBUG:graphein.protein.subgraphs:Found 10 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['D:HIS:335', 'D:LEU:332', 'D:ARG:331', 'D:MET:330', 'D:GLU:328', 'D:ARG:326', 'D:LEU:329', 'D:LEU:334', 'D:GLY:333', 'D:SER:327'].
DEBUG:graphein.protein.subgraphs:Found 8 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['D:LEU:332', 'D:ARG:331', 'D:MET:330', 'D:GLU:328', 'D:LEU:334', 'D:LEU:329', 'D:GLY:333', 'D:SER:327'].
DEBUG:graphein.protein.subgraphs:Found 8 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['D:LEU:332', 'D:ARG:331', 'D:MET:330', 'D:GLU:328', 'D:LEU:290', 'D:LEU:334', 'D:LEU:329', 'D:GLY:333'].
DEBUG:graphein.protein.subgraphs:Found 9 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['D:HIS:335', 'D:LEU:332', 'D:ARG:331', 'D:GLN:336', 'D:MET:330

DEBUG:graphein.protein.subgraphs:Found 9 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['D:GLU:358', 'D:ASP:363', 'D:PHE:364', 'D:PHE:365', 'D:ASP:361', 'D:GLY:360', 'D:ASP:357', 'D:GLN:359', 'D:GLU:362'].
DEBUG:graphein.protein.subgraphs:Found 9 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['D:GLU:358', 'D:ASP:363', 'D:PHE:364', 'D:PHE:365', 'D:ASP:366', 'D:ASP:361', 'D:GLY:360', 'D:GLN:359', 'D:GLU:362'].
DEBUG:graphein.protein.subgraphs:Found 12 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['D:ARG:322', 'D:ASP:363', 'D:LEU:367', 'D:LEU:319', 'D:PHE:364', 'D:PHE:365', 'D:ASP:366', 'D:ASP:361', 'D:VAL:323', 'D:GLY:360', 'D:GLN:359', 'D:GLU:362'].
DEBUG:graphein.protein.subgraphs:Found 12 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['D:ASP:36

DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['D:ASP:394', 'D:LYS:393', 'D:SER:395', 'D:ILE:387', 'D:LEU:389', 'D:VAL:392', 'D:THR:391', 'D:ILE:388', 'D:ASN:390'].
DEBUG:graphein.protein.subgraphs:Found 13 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['D:ASP:394', 'D:LYS:393', 'D:SER:395', 'D:PHE:401', 'D:ILE:387', 'D:LEU:389', 'D:VAL:392', 'D:GLU:398', 'D:LYS:396', 'D:THR:391', 'D:ILE:388', 'D:ALA:397', 'D:ASN:390'].
DEBUG:graphein.protein.subgraphs:Found 10 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['D:ASP:394', 'D:LYS:393', 'D:SER:395', 'D:LEU:389', 'D:VAL:392', 'D:GLU:398', 'D:THR:391', 'D:ILE:388', 'D:ALA:397', 'D:ASN:390'].
DEBUG:graphein.protein.subgraphs:Found 10 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['D:ASP:394', 'D:LYS:393', 'D:SER:395', 'D:LEU:389', 'D:VAL:392', 'D

DEBUG:graphein.protein.subgraphs:Found 9 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['D:ILE:425', 'D:GLU:426', 'D:GLN:420', 'D:PRO:419', 'D:TYR:421', 'D:TYR:422', 'D:GLU:427', 'D:LEU:424', 'D:LYS:423'].
DEBUG:graphein.protein.subgraphs:Found 9 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['D:CYS:428', 'D:ILE:425', 'D:GLU:426', 'D:GLN:420', 'D:TYR:421', 'D:TYR:422', 'D:GLU:427', 'D:LEU:424', 'D:LYS:423'].
DEBUG:graphein.protein.subgraphs:Found 9 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['D:CYS:428', 'D:VAL:429', 'D:ILE:425', 'D:GLU:426', 'D:TYR:421', 'D:TYR:422', 'D:GLU:427', 'D:LEU:424', 'D:LYS:423'].
DEBUG:graphein.protein.subgraphs:Found 9 nodes in the spatial point-radius subgraph.
DEBUG:graphein.protein.subgraphs:Creating subgraph from nodes: ['D:CYS:428', 'D:SER:430', 'D:VAL:429', 'D:ILE:425'

INFO:graphein.protein.utils:Downloaded PDB file for: 1z2c


In [13]:
print(len(example_pyg_list))

45


In [14]:
import pickle
with open(f"./example_pyg_surface_{RSA}.pkl", "wb") as f:
    pickle.dump(example_pyg_list, f)